# Imports

In [3]:
from surprise import NormalPredictor
from surprise.model_selection import train_test_split
from surprise import accuracy
import heapq
import pickle 
import pandas as pd
from surprise import Dataset
from surprise import Reader
from surprise import AlgoBase
from create_similarity_vectors import create_top_k_similar_vectors
from sentence_transformers import util
import torch

from surprise.prediction_algorithms.predictions import PredictionImpossible
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

# Constants

In [64]:
TOP_ING_CAT = "../word_embeddings_files/top25_ing_cat.obj"

RECIPES_WITH_RATINGS = "../samples/recipes_with_ratings.parquet"
RATINGS_SMALL = "../EDA_files/ratings_small.parquet"
WORD2VEC_ING_CAT_VECTORS = "../word_embeddings_files/vectors/word2vec_ing_cat_vectors.obj"

INDEX_TO_RECIPE_OBJ = "../samples/index_to_recipe_with_ratings.obj"
RECIPE_TO_INDEX_OBJ = "../samples/recipe_to_index_with_ratings.obj"

# Load data 

In [268]:
recipes_with_ratings = pd.read_parquet(RECIPES_WITH_RATINGS)
ratings_small = pd.read_parquet(RATINGS_SMALL)

with open(TOP_ING_CAT, 'rb') as input_file:
    top_ing_cat = pickle.load(input_file)

In [261]:
with open(WORD2VEC_ING_CAT_VECTORS, "rb") as input_file:
    word2vec_ing_cat_vectors = pickle.load(input_file)

In [262]:
with open(RECIPE_TO_INDEX_OBJ, "rb") as input_file:
    recipe_to_index = pickle.load(input_file)

In [269]:
ratings_small = ratings_small[ratings_small.RecipeId.isin(recipes_with_ratings.RecipeId)]

In [270]:
word2vec_ing_cat_vectors_sample = {}
for key, value in word2vec_ing_cat_vectors.items():
    if key in recipe_to_index.keys():
        word2vec_ing_cat_vectors_sample[key] = value

# Create dataset

In [277]:
ratings_small = ratings_small[['AuthorId', 'RecipeId', 'Rating']]

In [278]:
ratingsDataset = Dataset.load_from_df(ratings_small, Reader(rating_scale=(0,5)))

# Algorithm Class

In [289]:
class Word2VecAlgorithm(AlgoBase):
    def __init__(self, vectors, k=40, verbose=True):
        self.k = k
        self.verbose = True
        self.vectors = vectors
        try:
            self.type = sim_options['type']
        except:
            self.type = None
    def fit(self, trainset):
        AlgoBase.fit(self, trainset)
        return self
    
    def estimate(self, u, i):
        if not (self.trainset.knows_item(i)):
#             if(self.verbose):
#                 print('raise for ', u, ' ', i)
            raise PredictionImpossible('Item is unknown')
        if not (self.trainset.knows_user(u)):
            raise PredictionImpossible('User is unknown')
        
        neighbours = []
        for rating in self.trainset.ur[u]:
            tensor1 = torch.tensor(self.vectors[trainset.to_raw_iid(rating[0])], dtype=torch.float)
            tensor2 = torch.tensor(self.vectors[trainset.to_raw_iid(i)], dtype=torch.float)
                                       
            sim = util.pytorch_cos_sim(tensor1, tensor2)[0][0].item()
            neighbours.append((sim, rating[1]))
        
        # Top k most similar ratings:
        k_neighbors = heapq.nlargest(self.k, neighbours, key=lambda t: t[0])
        
        # Avg score of k neigbors weighted by user ratings
        #print('Total similarity')
        simTotal = weightedSum = 0
        for (simScore, rating) in k_neighbors:
            if (simScore > 0):
                simTotal += simScore
                weightedSum += simScore * rating

        
        if (simTotal == 0):
            raise PredictionImpossible('No neighbors')

        predictedRating = weightedSum / simTotal

        return predictedRating

In [290]:
class Word2VecMatrixAlgorithm(AlgoBase):
    '''
    1) Calculate matrix during train:
        index - inner item ids
    2) Use pre-calculated matrix:
        index - recipe_id_to_pos (first change inner id to raw id, and get position from recipe id)
    3) Use submatrix from pre-calculated matrix:
        index - inner item ids
    '''
    def __init__(self, vectors, matrix=None, recipe_id_to_pos=None, create_subset=False, k=40, verbose=True):
        self.k = k
        self.verbose = True
        self.vectors = vectors
        self.matrix = matrix
        self.recipe_id_to_pos = recipe_id_to_pos
        self.create_subset = create_subset
        if matrix == None:
            self.type = "calculate matrix"
        else:
            if create_subset:
                self.type = "subset"
            else:
                self.type = "precalculated matrix"

    def fit(self, trainset):
        AlgoBase.fit(self, trainset)
        if matrix != None:
            if self.create_subset:
                self.similarites = create_similarity_submatrix(self.matrix, 
                                                               self.recipe_id_to_pos_in_matrix, 
                                                               trainset)
            else:
                self.similarites = self.matrix
            del(self.matrix)
        else:
            calculate_sim_matrix(trainset)
        return self
    
    def estimate(self, u, i):
        if not (self.trainset.knows_item(i)):
#             if(self.verbose):
#                 print('raise for ', u, ' ', i)
            raise PredictionImpossible('Item is unknown')
        if not (self.trainset.knows_user(u)):
            raise PredictionImpossible('User is unknown')
        
        neighbours = []
        for rating in self.trainset.ur[u]:
            if self.type == "precalculated matrix":
                recipe_id1 = self.trainset.to_raw_iid(i)
                recipe_id2 = self.trainset.to_raw_iid(rating[0])
                
                sim = self.similarities[self.recipe_id_to_pos[recipe_id1],
                                       self.recipe_id_to_pos[recipe_id2]]
            else:
                sim = self.similarites[i, rating[0]]
            neighbours.append( (sim, rating[1]) )
        
        # Top k most similar ratings:
        k_neighbors = heapq.nlargest(self.k, neighbours, key=lambda t: t[0])
        
        # Avg score of k neigbors weighted by user ratings
        #print('Total similarity')
        simTotal = weightedSum = 0
        for (simScore, rating) in k_neighbors:
            if (simScore > 0):
                simTotal += simScore
                weightedSum += simScore * rating

        
        if (simTotal == 0):
            raise PredictionImpossible('No neighbors')

        predictedRating = weightedSum / simTotal

        return predictedRating
    
    def calculate_sim_matrix(trainset):
        if(self.verbose):
            print("Computing content-based similarity matrix...")
    
            #self.similarities = mat.Matrix(self.trainset.n_items)
            print('Number of items in trainset: ', trainset.n_items)   
            self.similarities = np.zeros((self.trainset.n_items, self.trainset.n_items))
            for thisRating in range(trainset.n_items):
                if (thisRating % 1000 == 0):
                        print(thisRating, " of ", self.trainset.n_items)
                for otherRating in range(thisRating+1, self.trainset.n_items):
                    thisRecipeID = int(self.trainset.to_raw_iid(thisRating))
                    otherRecipeID = int(self.trainset.to_raw_iid(otherRating))
                    #if(self.verbose):
                    #    print(thisRecipeID, "  ", otherRecipeID)
                    tensor1 = torch.tensor(self.vectors[thisRecipeID], dtype=torch.float)
                    tensor2 = torch.tensor(self.vectors[otherRecipeID], dtype=torch.float)

                    sim = util.pytorch_cos_sim(tensor1, tensor2)[0][0].item()
                    self.similarities[thisRating, otherRating] = sim
                    self.similarities[otherRating, thisRating] = sim
        
        
        if(self.verbose):
            print("...done.")
            
    def create_similarity_submatrix(matrix, recipe_id_to_pos_in_matrix, trainset):
        similarities = np.zeros((trainset.n_items, trainset.n_items))
        for thisRating in range(trainset.n_items):
            if (thisRating % 1000 == 0):
                print(thisRating, " of ", trainset.n_items)
            for otherRating in range(thisRating+1, trainset.n_items):
                thisRecipeID = int(trainset.to_raw_iid(thisRating))
                otherRecipeID = int(trainset.to_raw_iid(otherRating))
                pos1 = recipe_id_to_pos_in_matrix[thisRecipeID]
                pos2 = recipe_id_to_pos_in_matrix[otherRecipeID]

                sim = matrix[pos1, pos2]
                similarities[thisRating, otherRating] = sim
                similarities[otherRating, thisRating] = sim
        return similarities

In [4]:
class TopKVectorsAlgorithm(AlgoBase):
    def __init__(self, top_similar_dict, vectors_dict, k=40, verbose=True):
        self.k = k
        self.top_vectors_dict = top_vectors_dict
        slef.vectors_dict = vectors_dict
        
        
    def fit(self, trainset):
        AlgoBase.fit(self, trainset)
        
        return self
    
    def estimate(self, u, i):
        if not (self.trainset.knows_item(i)):
#             if(self.verbose):
#                 print('raise for ', u, ' ', i)
            raise PredictionImpossible('Item is unknown')
        if not (self.trainset.knows_user(u)):
            raise PredictionImpossible('User is unknown')
        
        i_recipe_id = self.trainset.to_raw_iid(i)
        if i_recipe_id not in self.top_vectors_dict.keys():
            raise PredictionImpossible('No similar recipes for item')
            
        neighbours = []
        for rating in self.trainset.ur[u]:
            other_recipe_id = self.trainset.to_raw_iid(rating[0])
            
            found=False
            for recipe, sim in self.top_vectors_dict[i_recipe_id]:
                if recipe == other_recipe_id:
                    neighbours.append((sim, rating[1]) )
                    found = True
                    break
            if not found:
                    tensor1 = torch.tensor(self.vectors[trainset.to_raw_iid(rating[0])], dtype=torch.float)
                    tensor2 = torch.tensor(self.vectors[i_recipe_id], dtype=torch.float)
                                       
                    sim = util.pytorch_cos_sim(tensor1, tensor2)[0][0].item()
                    neighbours.append((sim, rating[1]))
                    
        # Top k most similar ratings:
        k_neighbors = heapq.nlargest(self.k, neighbours, key=lambda t: t[0])
        
        # Avg score of k neigbors weighted by user ratings
        #print('Total similarity')
        simTotal = weightedSum = 0
        for (simScore, rating) in k_neighbors:
            if (simScore > 0):
                simTotal += simScore
                weightedSum += simScore * rating

        
        if (simTotal == 0):
            raise PredictionImpossible('No neighbors')

        predictedRating = weightedSum / simTotal

        return predictedRating

In [280]:
trainset, testset = train_test_split(ratingsDataset, test_size=0.75)

In [285]:
trainset.n_ratings

350490

In [286]:
knn = ContentBasedAlgorithm(word2vec_ing_cat_vectors_sample, sim_options={'type': 'word2vec'})
knn.fit(trainset)

In [287]:
predictions = knn.test(testset=testset)

raise for  1952   UKN__374374
raise for  114   UKN__23118
raise for  3092   UKN__157154
raise for  85   UKN__66295
raise for  9383   UKN__64572
raise for  37767   UKN__295328
raise for  1259   UKN__17741
raise for  170   UKN__62936
raise for  484   UKN__353555
raise for  1554   UKN__245280
raise for  2530   UKN__46778
raise for  7448   UKN__366761
raise for  3579   UKN__357158
raise for  UKN__2001637252   UKN__208115
raise for  1482   UKN__451995
raise for  385   UKN__364965
raise for  1387   UKN__483263
raise for  829   UKN__158171
raise for  45836   UKN__72209
raise for  41746   UKN__118256
raise for  946   UKN__317052
raise for  UKN__1401338   UKN__248904
raise for  63   UKN__154286
raise for  UKN__2001443157   UKN__153449
raise for  21   UKN__475432
raise for  228   UKN__456641
raise for  18182   UKN__291401
raise for  115   UKN__190460
raise for  4442   UKN__242219
raise for  7837   UKN__226896
raise for  UKN__898628   UKN__313130
raise for  7870   UKN__124244
raise for  21   UKN_

raise for  UKN__1800053673   UKN__189096
raise for  7935   UKN__364692
raise for  5453   UKN__93119
raise for  4692   UKN__379039
raise for  6814   UKN__413389
raise for  2293   UKN__220817
raise for  26126   UKN__145382
raise for  969   UKN__195668
raise for  38307   UKN__37714
raise for  UKN__2001544334   UKN__344269
raise for  UKN__49396   UKN__37041
raise for  23062   UKN__119312
raise for  2732   UKN__373341
raise for  21213   UKN__43455
raise for  114   UKN__96328
raise for  252   UKN__231583
raise for  27469   UKN__185007
raise for  UKN__583869   UKN__170477
raise for  115   UKN__340900
raise for  2898   UKN__183622
raise for  18965   UKN__365549
raise for  1037   UKN__173266
raise for  216   UKN__67936
raise for  8397   UKN__188387
raise for  379   UKN__44608
raise for  8691   UKN__182931
raise for  4893   UKN__247383
raise for  29716   UKN__361981
raise for  5159   UKN__232399
raise for  19782   UKN__412697
raise for  11975   UKN__366876
raise for  UKN__51393   UKN__123850
rai

raise for  3111   UKN__34241
raise for  13027   UKN__9437
raise for  170   UKN__152280
raise for  3113   UKN__323356
raise for  21   UKN__298012
raise for  14152   UKN__104271
raise for  409   UKN__75260
raise for  1516   UKN__293357
raise for  869   UKN__176094
raise for  272   UKN__60334
raise for  1679   UKN__391484
raise for  UKN__1811907   UKN__447688
raise for  UKN__2001305873   UKN__225773
raise for  1642   UKN__482570
raise for  85   UKN__78812
raise for  741   UKN__414575
raise for  145   UKN__252463
raise for  3558   UKN__292036
raise for  252   UKN__169699
raise for  21   UKN__339348
raise for  153   UKN__213944
raise for  7337   UKN__263505
raise for  1693   UKN__447175
raise for  191   UKN__241751
raise for  2164   UKN__50601
raise for  UKN__989117   UKN__138962
raise for  4233   UKN__55335
raise for  494   UKN__201369
raise for  9953   UKN__308461
raise for  414   UKN__38415
raise for  3148   UKN__492152
raise for  145   UKN__177470
raise for  15004   UKN__171716
raise fo

raise for  313   UKN__250982
raise for  2663   UKN__191491
raise for  6117   UKN__13138
raise for  3557   UKN__426424
raise for  32   UKN__169405
raise for  435   UKN__269286
raise for  637   UKN__228339
raise for  30332   UKN__453292
raise for  178   UKN__337113
raise for  3198   UKN__134146
raise for  UKN__1803580801   UKN__486242
raise for  697   UKN__475477
raise for  7068   UKN__178455
raise for  UKN__22820   UKN__10415
raise for  17   UKN__467068
raise for  178   UKN__430973
raise for  277   UKN__7145
raise for  114   UKN__450715
raise for  709   UKN__50344
raise for  8688   UKN__13080
raise for  6226   UKN__57983
raise for  60657   UKN__24776
raise for  61540   UKN__162345
raise for  6427   UKN__81016
raise for  113   UKN__327342
raise for  45   UKN__507013
raise for  3574   UKN__176679
raise for  1675   UKN__133180
raise for  2158   UKN__143083
raise for  195   UKN__397232
raise for  744   UKN__226801
raise for  UKN__2161033   UKN__482831
raise for  508   UKN__452701
raise for 

raise for  21   UKN__376734
raise for  185   UKN__48728
raise for  3203   UKN__70459
raise for  UKN__200673   UKN__41960
raise for  62539   UKN__438728
raise for  7116   UKN__183277
raise for  1322   UKN__183132
raise for  UKN__538494   UKN__22521
raise for  UKN__1668431   UKN__76350
raise for  42253   UKN__178633
raise for  20957   UKN__30859
raise for  495   UKN__124548
raise for  14414   UKN__89830
raise for  UKN__1188206   UKN__35531
raise for  74659   UKN__18048
raise for  UKN__55646   UKN__40842
raise for  5556   UKN__166362
raise for  313   UKN__289578
raise for  1267   UKN__206136
raise for  9020   UKN__322147
raise for  UKN__1029671   UKN__33766
raise for  1485   UKN__483103
raise for  13853   UKN__20555
raise for  4434   UKN__139242
raise for  168   UKN__178305
raise for  1441   UKN__287979
raise for  UKN__64549   UKN__26177
raise for  3656   UKN__151356
raise for  18011   UKN__65565
raise for  2232   UKN__136921
raise for  728   UKN__442894
raise for  5380   UKN__154088
rais

...

raise for  82   UKN__455411
raise for  40621   UKN__275258
raise for  UKN__2000838388   UKN__271410
raise for  11159   UKN__373834
raise for  893   UKN__67757
raise for  1007   UKN__383863
raise for  782   UKN__459305
raise for  21   UKN__260298
raise for  1266   UKN__57428
raise for  9837   UKN__9120
raise for  UKN__390074   UKN__3232
raise for  35849   UKN__430164
raise for  252   UKN__179811
raise for  193   UKN__394496
raise for  78260   UKN__425089
raise for  2042   UKN__226820
raise for  1478   UKN__56957
raise for  3632   UKN__294188
raise for  128   UKN__298314
raise for  1211   UKN__404956
raise for  1368   UKN__176355
raise for  632   UKN__365
raise for  UKN__2000676599   UKN__524613
raise for  888   UKN__359736
raise for  1387   UKN__378740
raise for  1898   UKN__276674
raise for  1189   UKN__198488
raise for  376   UKN__246834
raise for  UKN__1802388563   UKN__465746
raise for  1482   UKN__435259
raise for  854   UKN__232768
raise for  7789   UKN__385180
raise for  3049   U

raise for  14249   UKN__138620
raise for  18080   UKN__41752
raise for  UKN__1458895   UKN__279310
raise for  252   UKN__213749
raise for  47474   UKN__96156
raise for  1262   UKN__404558
raise for  211   UKN__187031
raise for  13562   UKN__193180
raise for  6753   UKN__223546
raise for  193   UKN__270448
raise for  192   UKN__66480
raise for  5091   UKN__97574
raise for  UKN__1802939513   UKN__98284
raise for  46677   UKN__330512
raise for  UKN__991820   UKN__222896
raise for  UKN__84941   UKN__55254
raise for  1999   UKN__409147
raise for  UKN__368327   UKN__239259
raise for  272   UKN__140841
raise for  72432   UKN__30416
raise for  329   UKN__22918
raise for  8379   UKN__26682
raise for  632   UKN__271909
raise for  1091   UKN__276822
raise for  75623   UKN__94694
raise for  UKN__2000276988   UKN__506597
raise for  78520   UKN__154714
raise for  204   UKN__508968
raise for  6243   UKN__186964
raise for  21   UKN__347862
raise for  6141   UKN__259827
raise for  UKN__2001499108   UKN

raise for  742   UKN__16678
raise for  2409   UKN__68310
raise for  313   UKN__370351
raise for  73137   UKN__19405
raise for  2900   UKN__424552
raise for  40973   UKN__83948
raise for  1905   UKN__492303
raise for  128   UKN__234701
raise for  634   UKN__377765
raise for  403   UKN__195217
raise for  93321   UKN__81652
raise for  UKN__88848   UKN__62443
raise for  144   UKN__261973
raise for  97780   UKN__64148
raise for  17   UKN__280211
raise for  8823   UKN__437392
raise for  2813   UKN__232750
raise for  46648   UKN__135
raise for  UKN__1824412   UKN__169870
raise for  34417   UKN__65120
raise for  2213   UKN__102004
raise for  484   UKN__277997
raise for  5969   UKN__36684
raise for  500   UKN__86060
raise for  7605   UKN__126199
raise for  74   UKN__265089
raise for  7155   UKN__450245
raise for  1760   UKN__365761
raise for  3794   UKN__77116
raise for  494   UKN__59889
raise for  5495   UKN__97977
raise for  28556   UKN__370750
raise for  857   UKN__304957
raise for  3174   U

raise for  6390   UKN__358785
raise for  1266   UKN__29435
raise for  151   UKN__183444
raise for  UKN__1408460   UKN__403676
raise for  2389   UKN__325245
raise for  13169   UKN__426862
raise for  381   UKN__334329
raise for  5032   UKN__382568
raise for  11697   UKN__454137
raise for  7135   UKN__235388
raise for  1766   UKN__188795
raise for  27874   UKN__124293
raise for  UKN__1481874   UKN__239061
raise for  UKN__2000698712   UKN__382218
raise for  1766   UKN__381856
raise for  UKN__1802511339   UKN__434616
raise for  37401   UKN__57461
raise for  42164   UKN__405691
raise for  829   UKN__466472
raise for  UKN__2002715562   UKN__97106
raise for  UKN__1599318   UKN__31681
raise for  1447   UKN__396067
raise for  2184   UKN__444211
raise for  942   UKN__359045
raise for  3768   UKN__30974
raise for  22029   UKN__19201
raise for  7240   UKN__38995
raise for  10631   UKN__106400
raise for  2312   UKN__399350
raise for  4499   UKN__82907
raise for  1384   UKN__110199
raise for  3333   

KeyboardInterrupt: 

In [248]:
len(word2vec_ing_cat_vectors_sample)

271674

In [291]:
DOC2VEC_ING_CAT_MODEL = "../word_embeddings_files/models/doc2vec_ing_cat_model.obj"
with open(DOC2VEC_ING_CAT_MODEL, "rb") as input_file:
    doc2vec_ing_cat_model = pickle.load(input_file)

In [303]:
recipes_with_ratings

RecipeId                                               Name  \
0             38                  Low-Fat Berry Blue Frozen Dessert   
1             39                                            Biryani   
2             40                                      Best Lemonade   
3             41                     Carina's Tofu-Vegetable Kebabs   
4             42                                       Cabbage Soup   
...          ...                                                ...   
522039    540899                        Butter Pecan Banana Muffins   
522139    541001                           Homemade Adobo Seasoning   
522167    541030  Everything but the Bagel Seasoning (Trader Joe...   
522330    541195                       The Most Refreshing Lemonade   
522431    541298                                   Homemade Ketchup   

          AuthorId  CookTimeInMinutes  PrepTimeInMinutes  TotalTimeInMinutes  \
0             1533             1440.0               45.0              1485.0   
1             1567               25.0              240.0               265.0   
2             1566                5.0               30.0                35.0   
3             1586               20.0             1440.0              1460.0   
4             1538               30.0               20.0                50.0   
...            ...                ...                ...                 ...   
522039     1827868               18.0               10.0                28.0   
522139      181781                1.0               15.0                16.0   
522167       50509                0.0                5.0                 5.0   
522330  2002848998                2.0                5.0                 7.0   
522431  2002848998                0.0                5.0                 5.0   

                   DatePublished  \
0      1999-08-09 21:46:00+00:00   
1      1999-08-29 13:12:00+00:00   
2      1999-09-05 19:52:00+00:00   
3      1999-09-03 14:54:00+00:00   
4      1999-09-19 06:19:00+00:00   
...                          ...   
522039 2020-09-01 20:59:00+00:00   
522139 2020-09-24 16:53:00+00:00   
522167 2020-10-02 20:48:00+00:00   
522330 2020-11-09 16:13:00+00:00   
522431 2020-11-30 18:03:00+00:00   

                                              Description   RecipeCategory  \
0       Make and share this Low-Fat Berry Blue Frozen ...  Frozen Desserts   
1       Make and share this Biryani recipe from Food.com.   Chicken Breast   
2       This is from one of my  first Good House Keepi...        Beverages   
3       This dish is best prepared a day in advance to...         Soy/Tofu   
4       Make and share this Cabbage Soup recipe from F...        Vegetable   
...                                                   ...              ...   
522039  Make and share this Butter Pecan Banana Muffin...           Breads   
522139  Make and share this Homemade Adobo Seasoning r...          Mexican   
522167  This is a copycat of this popular seasoning mi...        < 15 Mins   
522330  Lemonade is so refreshing. You won't believe h...        Beverages   
522431  Homemade ketchup is so easy and is made with j...        < 15 Mins   

                                                 Keywords  \
0       [Dessert, Low Protein, Low Cholesterol, Health...   
1       [Chicken Thigh & Leg, Chicken, Poultry, Meat, ...   
2       [Low Protein, Low Cholesterol, Healthy, Summer...   
3       [Beans, Vegetable, Low Cholesterol, Weeknight,...   
4       [Low Protein, Vegan, Low Cholesterol, Healthy,...   
...                                                   ...   
522039  [Breakfast, Brunch, < 30 Mins, Easy, From Scra...   
522139  [Low Cholesterol, High Fiber, Healthy, High In...   
522167                               [Easy, From Scratch]   
522330  [Low Protein, Low Cholesterol, Healthy, < 15 M...   
522431                                             [Easy]   

                                              Ingredients  RecipeServings  \
0       [blueb

In [316]:
doc2vec_ing_cat_model.dv.most_similar([44])

[(472391, 0.7484411597251892),
 (367916, 0.7208930850028992),
 (444007, 0.7046064138412476),
 (243247, 0.6813440322875977),
 (419388, 0.6721782684326172),
 (331655, 0.6677903532981873),
 (85677, 0.6611077189445496),
 (510373, 0.6596683263778687),
 (297676, 0.6589468121528625),
 (524506, 0.657532811164856)]

In [313]:
recipes_with_ratings[recipes_with_ratings.RecipeId==358825]

Empty DataFrame
Columns: [RecipeId, Name, AuthorId, CookTimeInMinutes, PrepTimeInMinutes, TotalTimeInMinutes, DatePublished, Description, RecipeCategory, Keywords, Ingredients, RecipeServings, RecipeInstructions, Nutritions]
Index: []